In [ ]:
!pip uninstall -y gcsfs
!pip install transformers datasets scikit-learn

Found existing installation: gcsfs 2024.10.0
Uninstalling gcsfs-2024.10.0:
  Successfully uninstalled gcsfs-2024.10.0


In [ ]:
import pandas as pd
import torch
from transformers import BertTokenizer, BertForSequenceClassification, AutoModelForSequenceClassification
from sklearn.metrics import accuracy_score, classification_report

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
# please manually adjust the data and model path for your customized testing
csv_file_path = '/content/drive/Shared drives/5190_NLP_Project/test_data_random_subset.csv'
model_path = '/content/drive/Shared drives/5190_NLP_Project/Bert_trained_model'

data = pd.read_csv(csv_file_path)

titles = data['title'].tolist()
labels = data['labels'].tolist()

labels = [1 if label == 0 else 0 for label in labels]

tokenizer = BertTokenizer.from_pretrained(model_path)
model = BertForSequenceClassification.from_pretrained(model_path)
model.eval()

encodings = tokenizer(
    titles,
    padding=True,
    truncation=True,
    max_length=128,
    return_tensors='pt'
)

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)
for key in encodings:
    encodings[key] = encodings[key].to(device)

with torch.no_grad():
    outputs = model(**encodings)
    logits = outputs.logits

predictions = torch.argmax(logits, dim=-1).cpu().numpy()

accuracy = accuracy_score(labels, predictions)
report = classification_report(labels, predictions)

print(f"Accuracy: {accuracy:.4f}")
print("\nClassification Report:\n", report)

Accuracy: 0.7000

Classification Report:
               precision    recall  f1-score   support

           0       0.83      0.50      0.62        10
           1       0.64      0.90      0.75        10

    accuracy                           0.70        20
   macro avg       0.74      0.70      0.69        20
weighted avg       0.74      0.70      0.69        20

